In [1]:
from unstructured.partition.pdf import partition_pdf

/home/rajeev-kumar/Desktop/Multimodal-summerizer/env/lib/python3.11/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
raw_data=partition_pdf(
    filename="/home/rajeev-kumar/Desktop/Multimodal-summerizer/data/student_handbook.pdf",
    strategy='hi_res',
    extract_images_in_pdf=True,
    extract_image_block_types=["Image", "Table"],
    extract_image_block_to_payload=False,
    extract_image_block_output_dir="extracted_data"
)

In [3]:
raw_data

In [6]:
for element in raw_data:
    print(type(element))
    break

<class 'unstructured.documents.elements.Image'>


In [8]:
Header=[]
Footer=[]
Title=[]
NarrativeText=[]
Text=[]
ListItem=[]
Table=[]
Image=[]

for element in raw_data:
  if "unstructured.documents.elements.Image" in str(type(element)):
            Image.append(str(element))
  elif "unstructured.documents.elements.Table" in str(type(element)):
            Table.append(str(element))
  elif "unstructured.documents.elements.Header" in str(type(element)):
            Header.append(str(element))
  elif "unstructured.documents.elements.Footer" in str(type(element)):
            Footer.append(str(element))
  elif "unstructured.documents.elements.Title" in str(type(element)):
            Title.append(str(element))
  elif "unstructured.documents.elements.NarrativeText" in str(type(element)):
            NarrativeText.append(str(element))
  elif "unstructured.documents.elements.Text" in str(type(element)):
            Text.append(str(element))
  elif "unstructured.documents.elements.ListItem" in str(type(element)):
            ListItem.append(str(element))





In [9]:
Table

['Terms Used .........................................................................................................................4 Scope ...................................................................................................................................5 Introduction .........................................................................................................................5 Academic Administration ...................................................................................................5 Dean of Academic Affairs (DOAA) .........................................................................................5 Institute Postgraduate Committee (IPGC) .............................................................................6 Institute Undergraduate Committee (IUGC) ...........................................................................6 Discipline Postgraduate Committee (DPGC) ...............................................................

In [10]:
Image

['',
 '_ Sa jie ert ® Sita %e S My X “tute of Teow™',
 'MlE4O1 a',
 'MlE4O1',
 'Code of the discipline/   category of course  ',
 'Unique identification code of   the course  ',
 'Level of the course   1 to 4: UG Course  ',
 'S   F  ']

In [11]:
NarrativeText

['(Applicable for students admitted till 2022-23-W semester)',
 'Indian Institute of Technology Bhilai',
 'The provisions of this handbook are applicable to students admitted till 2022-23-W semester in all programs and disciplines. The academic senate on the recommendation of the Dean of Academic Affairs may change any or all parts of this handbook at any time.',
 'IIT Bhilai offers a semester-oriented undergraduate, postgraduate and research programs with an objective of imparting best quality science and engineering education. Admissions to the academic programs are synchronized with an academic year, though in some cases, it may be synchronized to the start of a semester. An academic year starts in the month of July each calendar year and ends in the month of June of the next calendar year. Each academic year is divided into three semesters – Monsoon, Winter and Summer semesters. The Monsoon and Winter semesters are two regular semesters. The Summer semester is a shorter semester an

In [13]:
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import ChatPromptTemplate
from langchain.chat_models import init_chat_model

In [20]:
import os
from dotenv import load_dotenv

load_dotenv()

True

In [22]:
GOOGLE_API_KEY=os.getenv("GOOGLE_API_KEY")
os.environ["GOOGLE_API_KEY"]=GOOGLE_API_KEY

In [52]:
model=init_chat_model("gemini-2.5-flash", model_provider="google_genai")

In [26]:
res=model.invoke("Hello, world!")
res.content

"Hello there! It's a pleasure to connect with you. How can I help you today?"

###Table summery

In [ ]:
# Prompt
prompt_text = """You are an assistant tasked with summarizing tables for retrieval. \
    These summaries will be embedded and used to retrieve the raw table elements. \
    Give a concise summary of the table that is well optimized for retrieval. Table:{element} """

In [28]:
prompt = ChatPromptTemplate.from_template(prompt_text)

In [29]:
summarize_chain = {"element": lambda x: x} | prompt | model | StrOutputParser()

In [30]:
table_summaries = []
table_summaries = summarize_chain.batch(Table, {"max_concurrency": 5})
table_summaries

['This table serves as a table of contents or outline, detailing academic administration, programs, admissions, registration procedures, and related policies for IIT Bhilai.',
 'This table outlines an academic grading and evaluation system, detailing grades for regular courses, thesis, and audited courses, along with CGPA/SGPA calculation, course repetition, thesis evaluation, and candidacy examination. It also covers industrial training, awards, fellowships, definitions, and policies related to academic procedures.',
 'This table defines various academic terms and concepts used within an educational institution. It includes definitions for degree programs (Undergraduate, Postgraduate), academic governance bodies (Academic Senate, IPGC), administrative roles (DOAA, DOSA), academic calendar components (Academic Year, Semesters), organizational units (Department, Discipline), and student performance indicators (Grade).',
 'This table defines key academic and student governance terms. It 

###Text summery

In [32]:
# Prompt
prompt_text = """You are an assistant tasked with summarizing text for retrieval. \
    These summaries will be embedded and used to retrieve the raw text elements. \
    Give a concise summary of the table or text that is well optimized for retrieval.text: {element} """

In [ ]:
prompt = ChatPromptTemplate.from_template(prompt_text)

In [53]:
summarize_chain = {"element": lambda x: x} | prompt | model | StrOutputParser()

In [45]:
len(NarrativeText)

89

In [55]:
import time

text_summaries = []
batch_size = 5  # safely under your quota
for i in range(0, len(NarrativeText), batch_size):
    batch = NarrativeText[i:i+batch_size]
    results = summarize_chain.batch(batch, {"max_concurrency": 5})
    text_summaries.extend(results)
    
    # wait 60 seconds if more batches are left
    if i + batch_size < len(NarrativeText):
        print("Waiting to respect API quota...")
        time.sleep(60)


Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...


In [57]:
text_summaries

['Applicable to students admitted through the 2022-23-W semester.',
 'Indian Institute of Technology Bhilai',
 'This handbook applies to students admitted until the 2022-23-W semester across all programs and disciplines. The Academic Senate, advised by the Dean of Academic Affairs, can modify its provisions at any time.',
 'IIT Bhilai offers undergraduate (BTech), postgraduate (MSc, MTech), and research (PhD) programs in science and engineering. The academic year runs from July to June, divided into Monsoon, Winter, and a shorter Summer semester. Admissions are synchronized with the academic year or semester start, and English is the medium of instruction for all programs.',
 'The Academic Senate is the supreme body governing all academic matters, including setting the Academic Calendar. The Dean of Academic Affairs oversees academic programs. Academic matters fall under IPGC/IUGC at the institute level and DPGC/DUGC at the department level. The Dean of Students’ Affairs manages studen

###Image Summary

In [58]:
import base64
from langchain_core.messages import HumanMessage,SystemMessage

In [59]:
def encode_image(image_path):
    """Getting the base64 string"""
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode("utf-8")

In [60]:
def image_summarize(img_base64, prompt):
    """Make image summary"""
    chat = init_chat_model("gemini-2.5-flash", model_provider="google_genai")

    msg = chat.invoke(
        [
            HumanMessage(
                content=[
                    {"type": "text", "text": prompt},
                    {
                        "type": "image_url",
                        "image_url": {"url": f"data:image/jpeg;base64,{img_base64}"},
                    },
                ]
            )
        ]
    )
    return msg.content

In [66]:
def generate_img_summaries(path):
    """
    Generate summaries and base64 encoded strings for images
    path: Path to list of .jpg files extracted by Unstructured
    """

    # Store base64 encoded images
    img_base64_list = []

    # Store image summaries
    image_summaries = []

    # Prompt
    prompt = """You are an assistant tasked with summarizing images for retrieval. \
    These summaries will be embedded and used to retrieve the raw image. \
    Give a concise summary of the image that is well optimized for retrieval."""

    # Apply to images
    i=0
    for img_file in sorted(os.listdir(path)):
        if i==5:
            i=0
            print("Waiting to respect API quota...")
            time.sleep(60)

            
        if img_file.endswith(".jpg"):
            img_path = os.path.join(path, img_file)
            base64_image = encode_image(img_path)
            img_base64_list.append(base64_image)
            image_summaries.append(image_summarize(base64_image, prompt))
            i=i+1


    return img_base64_list, image_summaries

In [63]:
fpath="/home/rajeev-kumar/Desktop/Multimodal-summerizer/notebook/extracted_data"

In [67]:
img_base64_list, image_summaries = generate_img_summaries(fpath)


Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...
Waiting to respect API quota...


In [68]:
image_summaries

['A large group of approximately 25-30 young men, appearing to be college students, pose for a group photo on an indoor staircase with white railings. Many are of South Asian descent, and one student in the foreground wears a dark blue t-shirt with "BHILAI" printed on it.',
 "Official logo of the Indian Institute of Technology Bhilai (IIT Bhilai). This circular emblem features a stylized purple globe grid at its center, surrounded by a hexagonal arrangement of arrows pointing inwards. The institution's name is inscribed in both English and Hindi script around the border, all on a white background.",
 'An image displaying the text "ME401" in a bold, outlined font on a white background. The text is annotated with an open bracket under "ME", a closing bracket under "401", and an upward arrow pointing to the "4".',
 'The text "ME401" in white with a black outline and drop shadow.',
 'Text displaying "Code of the discipline/ category of course", likely a header from an educational document 

In [69]:
img_base64_list

['...']

###Creating a MultiVector Retriever

In [3]:
import uuid

from langchain.retrievers.multi_vector import MultiVectorRetriever
from langchain.storage import InMemoryStore
from langchain_chroma import Chroma
from langchain_core.documents import Document
# from langchain_ import OpenAIEmbeddings
from langchain_google_genai import GoogleGenerativeAIEmbeddings

In [4]:
vectorstore = Chroma(
    collection_name="mm_rag", embedding_function=GoogleGenerativeAIEmbeddings(model='models/gemini-embedding-exp-03-07')
)

In [ ]:
def create_multi_vector_retriever(vectorstore, text_summaries, texts, table_summaries, tables, image_summaries, images):
    """
    Create retriever that indexes summaries, but returns raw images or texts
    """

    # Initialize the storage layer
    store = InMemoryStore()
    id_key = "doc_id"

    # Create the multi-vector retriever
    retriever = MultiVectorRetriever(
        vectorstore=vectorstore,
        docstore=store,
        id_key=id_key,
    )


    # Helper function to add documents to the vectorstore and docstore
    def add_documents(retriever, doc_summaries, doc_contents):

      doc_ids = [str(uuid.uuid4()) for _ in doc_contents]

      summary_docs = [
              Document(page_content=s, metadata={id_key: doc_ids[i]})
              for i, s in enumerate(doc_summaries)
          ]

      retriever.vectorstore.add_documents(summary_docs)
      retriever.docstore.mset(list(zip(doc_ids, doc_contents)))

      # Add texts, tables, and images
      # Check that text_summaries is not empty before adding
      if text_summaries:
          add_documents(retriever, text_summaries, texts)
      # Check that table_summaries is not empty before adding
      if table_summaries:
          add_documents(retriever, table_summaries, tab)
      # Check that image_summaries is not empty before adding
      if image_summaries:
          add_documents(retriever, image_summaries, img)

    return retriever

vectorstore = Chroma(
    collection_name="mm_rag", embedding_function=GoogleGenerativeAIEmbeddings(model='models/gemini-embedding-exp-03-07')
)

# Create retriever
retriever_multi_vector_img = create_multi_vector_retriever(
    vectorstore,
    text_summaries,
    Text,
    table_summaries,
    Table,
    image_summaries,
    img_base64_list,
)